In [81]:
# Dependencies
# ----------------------------------
import pandas as pd
import os
from numpy import genfromtxt
from time import time
from datetime import datetime
from sqlalchemy.ext.declarative import declarative_base
from sqlalchemy.ext.automap import automap_base
from sqlalchemy import create_engine
from sqlalchemy.orm import sessionmaker, Session

# Allow us to declare column types
from sqlalchemy import Column, Integer, String, Float, Date

In [82]:
import xml.etree.ElementTree as et 

xtree = et.parse("../data/r539cy.xml")
xroot = xtree.getroot()

In [83]:
df_cols = ["state", "file_week_ended", "initial_claims", "reflecting_week_ended", "continued_claims", "covered_employment", "insured_unemployment_rate"]
rows = []

for node in xroot: 
    s_state = node.find("stateName").text if node is not None else None
    s_file_week_ended = node.find("weekEnded").text if node is not None else None
    s_initial_claims = node.find("InitialClaims").text if node is not None else None
    s_reflecting_week_ended = node.find("ReflectingWeekEnded").text if node is not None else None
    s_continued_claims = node.find("ContinuedClaims").text if node is not None else None
    s_covered_employment = node.find("CoveredEmployment").text if node is not None else None
    s_insured_unemployment_rate = node.find("InsuredUnemploymentRate").text if node is not None else None
    
    rows.append({"state": s_state, "file_week_ended": s_file_week_ended, 
                 "initial_claims": s_initial_claims, "reflecting_week_ended": s_reflecting_week_ended,
                "continued_claims": s_continued_claims, "covered_employment": s_covered_employment,
                "insured_unemployment_rate": s_insured_unemployment_rate})

out_df = pd.DataFrame(rows, columns = df_cols)
out_df

state file_week_ended initial_claims reflecting_week_ended  \
0      Alabama      01/07/1995         21,321            12/31/1994   
1      Alabama      01/14/1995         22,338            01/07/1995   
2      Alabama      01/21/1995          6,397            01/14/1995   
3      Alabama      01/28/1995          6,139            01/21/1995   
4      Alabama      02/04/1995          5,307            01/28/1995   
...        ...             ...            ...                   ...   
70220  Wyoming      04/25/2020          3,497            04/18/2020   
70221  Wyoming      05/02/2020          2,854            04/25/2020   
70222  Wyoming      05/09/2020          3,297            05/02/2020   
70223  Wyoming      05/16/2020          2,303            05/09/2020   
70224  Wyoming      05/23/2020          2,800            05/16/2020   

      continued_claims covered_employment insured_unemployment_rate  
0               47,243          1,627,509                      2.90  
1               48,429          1,635,392                      2.96  
2               31,385          1,635,392                      1.92  
3               32,269          1,635,392                      1.97  
4               30,927          1,635,392                      1.89  
...                ...                ...                       ...  
70220           16,566            270,013                      6.14  
70221           17,521            270,013                      6.49  
70222           17,928            270,013                      6.64  
70223           17,335            270,013                      6.42  
70224           17,631            270,013                      6.53  

[70225 rows x 7 columns]

In [84]:
stateAbbrLookup = pd.read_json("../data/stateData.json")
stateAbbrLookup.head()

state  latitude  longitude abbr
0     Alabama   32.7990   -86.8073   AL
1      Alaska   61.3850  -152.2683   AK
2     Arizona   33.7712  -111.3877   AZ
3    Arkansas   34.9513   -92.3809   AR
4  California   36.1700  -119.7462   CA

In [85]:
types = stateAbbrLookup.dtypes
print(types)

state         object
latitude     float64
longitude    float64
abbr          object
dtype: object


In [86]:
stateUnempDF = out_df.join(stateAbbrLookup.set_index("state"), on="state", how="inner")
stateUnempDF = stateUnempDF.rename(columns = {"abbr":"state_abbr"})
stateUnempDF = stateUnempDF.dropna()

In [87]:
stateUnempDF['file_week_ended'] = pd.to_datetime(stateUnempDF.file_week_ended)
stateUnempDF['reflecting_week_ended'] = pd.to_datetime(stateUnempDF.reflecting_week_ended)
stateUnempDF.dtypes

state                                object
file_week_ended              datetime64[ns]
initial_claims                       object
reflecting_week_ended        datetime64[ns]
continued_claims                     object
covered_employment                   object
insured_unemployment_rate            object
latitude                            float64
longitude                           float64
state_abbr                           object
dtype: object

In [88]:
# establishes automap base connection to existing Project2.db
Base = automap_base()
print(Base)

engine = create_engine('sqlite:///../app/Project2.db')
Base.prepare(engine, reflect=True)

# check for unemploymentData table existence
unemployment = dir(Base.classes.unemploymentData)
print(unemployment)

<class 'sqlalchemy.ext.automap.Base'>
['__abstract__', '__class__', '__delattr__', '__dict__', '__dir__', '__doc__', '__eq__', '__format__', '__ge__', '__getattribute__', '__gt__', '__hash__', '__init__', '__init_subclass__', '__le__', '__lt__', '__mapper__', '__module__', '__ne__', '__new__', '__reduce__', '__reduce_ex__', '__repr__', '__setattr__', '__sizeof__', '__str__', '__subclasshook__', '__table__', '__weakref__', '_decl_class_registry', '_sa_class_manager', '_sa_decl_prepare', '_sa_raise_deferred_config', 'classes', 'continued_claims', 'covered_employment', 'file_week_ended', 'id', 'initial_claims', 'insured_unemployment_rate', 'metadata', 'prepare', 'reflecting_week_ended', 'state', 'state_abbr']


In [89]:
# drop the unemploymentData table within database

Base.classes.unemploymentData.__table__.drop(engine)

In [90]:
# Sets an object to utilize declarative base
Base = declarative_base()


# Creates Classes which will serve as the anchor points for our Tables -- not the table yet
class unemployment(Base):
    __tablename__ = 'unemploymentData'
    id = Column(Integer, primary_key=True)
    state = Column(String(20))
    file_week_ended = Column(Date)
    initial_claims = Column(Integer)
    reflecting_week_ended = Column(Date)
    continued_claims = Column(Integer)
    covered_employment = Column(Integer)
    insured_unemployment_rate = Column(Float)
    latitude = Column(Float)
    longitude = Column(Float)
    state_abbr = Column(String(3))

In [91]:
# this line formally creates the table in the database
Base.metadata.create_all(engine)

In [92]:
session = Session(engine)
t = time()

try:

    for index, row in stateUnempDF.iterrows():
        record = unemployment(**{
            'state' : row["state"],
            'file_week_ended' : row["file_week_ended"],
            'initial_claims' : row["initial_claims"],
            'reflecting_week_ended' : row["reflecting_week_ended"],
            'continued_claims' : row["continued_claims"],
            'covered_employment' : row["covered_employment"],
            'insured_unemployment_rate' : row["insured_unemployment_rate"],
            'latitude' : row["latitude"],
            'longitude' : row["longitude"],
            'state_abbr' : row["state_abbr"],
        })
        session.add(record) #Add all the records
        print(row["state"], row["file_week_ended"])

    session.commit() #Attempt to commit all the records
except(error):
    session.rollback() #Rollback the changes on error
    print(error)
finally:
    session.close() #Close the connection

Alabama 1995-01-07 00:00:00
Alabama 1995-01-14 00:00:00
Alabama 1995-01-21 00:00:00
Alabama 1995-01-28 00:00:00
Alabama 1995-02-04 00:00:00
Alabama 1995-02-11 00:00:00
Alabama 1995-02-18 00:00:00
Alabama 1995-02-25 00:00:00
Alabama 1995-03-04 00:00:00
Alabama 1995-03-11 00:00:00
Alabama 1995-03-18 00:00:00
Alabama 1995-03-25 00:00:00
Alabama 1995-04-01 00:00:00
Alabama 1995-04-08 00:00:00
Alabama 1995-04-15 00:00:00
Alabama 1995-04-22 00:00:00
Alabama 1995-04-29 00:00:00
Alabama 1995-05-06 00:00:00
Alabama 1995-05-13 00:00:00
Alabama 1995-05-20 00:00:00
Alabama 1995-05-27 00:00:00
Alabama 1995-06-03 00:00:00
Alabama 1995-06-10 00:00:00
Alabama 1995-06-17 00:00:00
Alabama 1995-06-24 00:00:00
Alabama 1995-07-01 00:00:00
Alabama 1995-07-08 00:00:00
Alabama 1995-07-15 00:00:00
Alabama 1995-07-22 00:00:00
Alabama 1995-07-29 00:00:00
Alabama 1995-08-05 00:00:00
Alabama 1995-08-12 00:00:00
Alabama 1995-08-19 00:00:00
Alabama 1995-08-26 00:00:00
Alabama 1995-09-02 00:00:00
Alabama 1995-09-09 0

Alabama 2001-06-30 00:00:00
Alabama 2001-07-07 00:00:00
Alabama 2001-07-14 00:00:00
Alabama 2001-07-21 00:00:00
Alabama 2001-07-28 00:00:00
Alabama 2001-08-04 00:00:00
Alabama 2001-08-11 00:00:00
Alabama 2001-08-18 00:00:00
Alabama 2001-08-25 00:00:00
Alabama 2001-09-01 00:00:00
Alabama 2001-09-08 00:00:00
Alabama 2001-09-15 00:00:00
Alabama 2001-09-22 00:00:00
Alabama 2001-09-29 00:00:00
Alabama 2001-10-06 00:00:00
Alabama 2001-10-13 00:00:00
Alabama 2001-10-20 00:00:00
Alabama 2001-10-27 00:00:00
Alabama 2001-11-03 00:00:00
Alabama 2001-11-10 00:00:00
Alabama 2001-11-17 00:00:00
Alabama 2001-11-24 00:00:00
Alabama 2001-12-01 00:00:00
Alabama 2001-12-08 00:00:00
Alabama 2001-12-15 00:00:00
Alabama 2001-12-22 00:00:00
Alabama 2001-12-29 00:00:00
Alabama 2002-01-05 00:00:00
Alabama 2002-01-12 00:00:00
Alabama 2002-01-19 00:00:00
Alabama 2002-01-26 00:00:00
Alabama 2002-02-02 00:00:00
Alabama 2002-02-09 00:00:00
Alabama 2002-02-16 00:00:00
Alabama 2002-02-23 00:00:00
Alabama 2002-03-02 0

Alabama 2013-04-27 00:00:00
Alabama 2013-05-04 00:00:00
Alabama 2013-05-11 00:00:00
Alabama 2013-05-18 00:00:00
Alabama 2013-05-25 00:00:00
Alabama 2013-06-01 00:00:00
Alabama 2013-06-08 00:00:00
Alabama 2013-06-15 00:00:00
Alabama 2013-06-22 00:00:00
Alabama 2013-06-29 00:00:00
Alabama 2013-07-06 00:00:00
Alabama 2013-07-13 00:00:00
Alabama 2013-07-20 00:00:00
Alabama 2013-07-27 00:00:00
Alabama 2013-08-03 00:00:00
Alabama 2013-08-10 00:00:00
Alabama 2013-08-17 00:00:00
Alabama 2013-08-24 00:00:00
Alabama 2013-08-31 00:00:00
Alabama 2013-09-07 00:00:00
Alabama 2013-09-14 00:00:00
Alabama 2013-09-21 00:00:00
Alabama 2013-09-28 00:00:00
Alabama 2013-10-05 00:00:00
Alabama 2013-10-12 00:00:00
Alabama 2013-10-19 00:00:00
Alabama 2013-10-26 00:00:00
Alabama 2013-11-02 00:00:00
Alabama 2013-11-09 00:00:00
Alabama 2013-11-16 00:00:00
Alabama 2013-11-23 00:00:00
Alabama 2013-11-30 00:00:00
Alabama 2013-12-07 00:00:00
Alabama 2013-12-14 00:00:00
Alabama 2013-12-21 00:00:00
Alabama 2013-12-28 0

Alabama 2019-11-23 00:00:00
Alabama 2019-11-30 00:00:00
Alabama 2019-12-07 00:00:00
Alabama 2019-12-14 00:00:00
Alabama 2019-12-21 00:00:00
Alabama 2019-12-28 00:00:00
Alabama 2020-01-04 00:00:00
Alabama 2020-01-11 00:00:00
Alabama 2020-01-18 00:00:00
Alabama 2020-01-25 00:00:00
Alabama 2020-02-01 00:00:00
Alabama 2020-02-08 00:00:00
Alabama 2020-02-15 00:00:00
Alabama 2020-02-22 00:00:00
Alabama 2020-02-29 00:00:00
Alabama 2020-03-07 00:00:00
Alabama 2020-03-14 00:00:00
Alabama 2020-03-21 00:00:00
Alabama 2020-03-28 00:00:00
Alabama 2020-04-04 00:00:00
Alabama 2020-04-11 00:00:00
Alabama 2020-04-18 00:00:00
Alabama 2020-04-25 00:00:00
Alabama 2020-05-02 00:00:00
Alabama 2020-05-09 00:00:00
Alabama 2020-05-16 00:00:00
Alabama 2020-05-23 00:00:00
Alaska 1995-01-07 00:00:00
Alaska 1995-01-14 00:00:00
Alaska 1995-01-21 00:00:00
Alaska 1995-01-28 00:00:00
Alaska 1995-02-04 00:00:00
Alaska 1995-02-11 00:00:00
Alaska 1995-02-18 00:00:00
Alaska 1995-02-25 00:00:00
Alaska 1995-03-04 00:00:00
A

Alaska 2006-01-14 00:00:00
Alaska 2006-01-21 00:00:00
Alaska 2006-01-28 00:00:00
Alaska 2006-02-04 00:00:00
Alaska 2006-02-11 00:00:00
Alaska 2006-02-18 00:00:00
Alaska 2006-02-25 00:00:00
Alaska 2006-03-04 00:00:00
Alaska 2006-03-11 00:00:00
Alaska 2006-03-18 00:00:00
Alaska 2006-03-25 00:00:00
Alaska 2006-04-01 00:00:00
Alaska 2006-04-08 00:00:00
Alaska 2006-04-15 00:00:00
Alaska 2006-04-22 00:00:00
Alaska 2006-04-29 00:00:00
Alaska 2006-05-06 00:00:00
Alaska 2006-05-13 00:00:00
Alaska 2006-05-20 00:00:00
Alaska 2006-05-27 00:00:00
Alaska 2006-06-03 00:00:00
Alaska 2006-06-10 00:00:00
Alaska 2006-06-17 00:00:00
Alaska 2006-06-24 00:00:00
Alaska 2006-07-01 00:00:00
Alaska 2006-07-08 00:00:00
Alaska 2006-07-15 00:00:00
Alaska 2006-07-22 00:00:00
Alaska 2006-07-29 00:00:00
Alaska 2006-08-05 00:00:00
Alaska 2006-08-12 00:00:00
Alaska 2006-08-19 00:00:00
Alaska 2006-08-26 00:00:00
Alaska 2006-09-02 00:00:00
Alaska 2006-09-09 00:00:00
Alaska 2006-09-16 00:00:00
Alaska 2006-09-23 00:00:00
A

...

Wisconsin 2008-11-29 00:00:00
Wisconsin 2008-12-06 00:00:00
Wisconsin 2008-12-13 00:00:00
Wisconsin 2008-12-20 00:00:00
Wisconsin 2008-12-27 00:00:00
Wisconsin 2009-01-03 00:00:00
Wisconsin 2009-01-10 00:00:00
Wisconsin 2009-01-17 00:00:00
Wisconsin 2009-01-24 00:00:00
Wisconsin 2009-01-31 00:00:00
Wisconsin 2009-02-07 00:00:00
Wisconsin 2009-02-14 00:00:00
Wisconsin 2009-02-21 00:00:00
Wisconsin 2009-02-28 00:00:00
Wisconsin 2009-03-07 00:00:00
Wisconsin 2009-03-14 00:00:00
Wisconsin 2009-03-21 00:00:00
Wisconsin 2009-03-28 00:00:00
Wisconsin 2009-04-04 00:00:00
Wisconsin 2009-04-11 00:00:00
Wisconsin 2009-04-18 00:00:00
Wisconsin 2009-04-25 00:00:00
Wisconsin 2009-05-02 00:00:00
Wisconsin 2009-05-09 00:00:00
Wisconsin 2009-05-16 00:00:00
Wisconsin 2009-05-23 00:00:00
Wisconsin 2009-05-30 00:00:00
Wisconsin 2009-06-06 00:00:00
Wisconsin 2009-06-13 00:00:00
Wisconsin 2009-06-20 00:00:00
Wisconsin 2009-06-27 00:00:00
Wisconsin 2009-07-04 00:00:00
Wisconsin 2009-07-11 00:00:00
Wisconsin 

Wisconsin 2015-01-31 00:00:00
Wisconsin 2015-02-07 00:00:00
Wisconsin 2015-02-14 00:00:00
Wisconsin 2015-02-21 00:00:00
Wisconsin 2015-02-28 00:00:00
Wisconsin 2015-03-07 00:00:00
Wisconsin 2015-03-14 00:00:00
Wisconsin 2015-03-21 00:00:00
Wisconsin 2015-03-28 00:00:00
Wisconsin 2015-04-04 00:00:00
Wisconsin 2015-04-11 00:00:00
Wisconsin 2015-04-18 00:00:00
Wisconsin 2015-04-25 00:00:00
Wisconsin 2015-05-02 00:00:00
Wisconsin 2015-05-09 00:00:00
Wisconsin 2015-05-16 00:00:00
Wisconsin 2015-05-23 00:00:00
Wisconsin 2015-05-30 00:00:00
Wisconsin 2015-06-06 00:00:00
Wisconsin 2015-06-13 00:00:00
Wisconsin 2015-06-20 00:00:00
Wisconsin 2015-06-27 00:00:00
Wisconsin 2015-07-04 00:00:00
Wisconsin 2015-07-11 00:00:00
Wisconsin 2015-07-18 00:00:00
Wisconsin 2015-07-25 00:00:00
Wisconsin 2015-08-01 00:00:00
Wisconsin 2015-08-08 00:00:00
Wisconsin 2015-08-15 00:00:00
Wisconsin 2015-08-22 00:00:00
Wisconsin 2015-08-29 00:00:00
Wisconsin 2015-09-05 00:00:00
Wisconsin 2015-09-12 00:00:00
Wisconsin 

Wyoming 1995-05-13 00:00:00
Wyoming 1995-05-20 00:00:00
Wyoming 1995-05-27 00:00:00
Wyoming 1995-06-03 00:00:00
Wyoming 1995-06-10 00:00:00
Wyoming 1995-06-17 00:00:00
Wyoming 1995-06-24 00:00:00
Wyoming 1995-07-01 00:00:00
Wyoming 1995-07-08 00:00:00
Wyoming 1995-07-15 00:00:00
Wyoming 1995-07-22 00:00:00
Wyoming 1995-07-29 00:00:00
Wyoming 1995-08-05 00:00:00
Wyoming 1995-08-12 00:00:00
Wyoming 1995-08-19 00:00:00
Wyoming 1995-08-26 00:00:00
Wyoming 1995-09-02 00:00:00
Wyoming 1995-09-09 00:00:00
Wyoming 1995-09-16 00:00:00
Wyoming 1995-09-23 00:00:00
Wyoming 1995-09-30 00:00:00
Wyoming 1995-10-07 00:00:00
Wyoming 1995-10-14 00:00:00
Wyoming 1995-10-21 00:00:00
Wyoming 1995-10-28 00:00:00
Wyoming 1995-11-04 00:00:00
Wyoming 1995-11-11 00:00:00
Wyoming 1995-11-18 00:00:00
Wyoming 1995-11-25 00:00:00
Wyoming 1995-12-02 00:00:00
Wyoming 1995-12-09 00:00:00
Wyoming 1995-12-16 00:00:00
Wyoming 1995-12-23 00:00:00
Wyoming 1995-12-30 00:00:00
Wyoming 1996-01-06 00:00:00
Wyoming 1996-01-13 0

Wyoming 2001-02-03 00:00:00
Wyoming 2001-02-10 00:00:00
Wyoming 2001-02-17 00:00:00
Wyoming 2001-02-24 00:00:00
Wyoming 2001-03-03 00:00:00
Wyoming 2001-03-10 00:00:00
Wyoming 2001-03-17 00:00:00
Wyoming 2001-03-24 00:00:00
Wyoming 2001-03-31 00:00:00
Wyoming 2001-04-07 00:00:00
Wyoming 2001-04-14 00:00:00
Wyoming 2001-04-21 00:00:00
Wyoming 2001-04-28 00:00:00
Wyoming 2001-05-05 00:00:00
Wyoming 2001-05-12 00:00:00
Wyoming 2001-05-19 00:00:00
Wyoming 2001-05-26 00:00:00
Wyoming 2001-06-02 00:00:00
Wyoming 2001-06-09 00:00:00
Wyoming 2001-06-16 00:00:00
Wyoming 2001-06-23 00:00:00
Wyoming 2001-06-30 00:00:00
Wyoming 2001-07-07 00:00:00
Wyoming 2001-07-14 00:00:00
Wyoming 2001-07-21 00:00:00
Wyoming 2001-07-28 00:00:00
Wyoming 2001-08-04 00:00:00
Wyoming 2001-08-11 00:00:00
Wyoming 2001-08-18 00:00:00
Wyoming 2001-08-25 00:00:00
Wyoming 2001-09-01 00:00:00
Wyoming 2001-09-08 00:00:00
Wyoming 2001-09-15 00:00:00
Wyoming 2001-09-22 00:00:00
Wyoming 2001-09-29 00:00:00
Wyoming 2001-10-06 0

Wyoming 2014-02-01 00:00:00
Wyoming 2014-02-08 00:00:00
Wyoming 2014-02-15 00:00:00
Wyoming 2014-02-22 00:00:00
Wyoming 2014-03-01 00:00:00
Wyoming 2014-03-08 00:00:00
Wyoming 2014-03-15 00:00:00
Wyoming 2014-03-22 00:00:00
Wyoming 2014-03-29 00:00:00
Wyoming 2014-04-05 00:00:00
Wyoming 2014-04-12 00:00:00
Wyoming 2014-04-19 00:00:00
Wyoming 2014-04-26 00:00:00
Wyoming 2014-05-03 00:00:00
Wyoming 2014-05-10 00:00:00
Wyoming 2014-05-17 00:00:00
Wyoming 2014-05-24 00:00:00
Wyoming 2014-05-31 00:00:00
Wyoming 2014-06-07 00:00:00
Wyoming 2014-06-14 00:00:00
Wyoming 2014-06-21 00:00:00
Wyoming 2014-06-28 00:00:00
Wyoming 2014-07-05 00:00:00
Wyoming 2014-07-12 00:00:00
Wyoming 2014-07-19 00:00:00
Wyoming 2014-07-26 00:00:00
Wyoming 2014-08-02 00:00:00
Wyoming 2014-08-09 00:00:00
Wyoming 2014-08-16 00:00:00
Wyoming 2014-08-23 00:00:00
Wyoming 2014-08-30 00:00:00
Wyoming 2014-09-06 00:00:00
Wyoming 2014-09-13 00:00:00
Wyoming 2014-09-20 00:00:00
Wyoming 2014-09-27 00:00:00
Wyoming 2014-10-04 0

In [93]:
#Create the session
session = sessionmaker()
session.configure(bind=engine)
s = session()

data = s.query(unemployment)
for row in data:
    print(row.file_week_ended)

s.close()

1995-01-07
1995-01-14
1995-01-21
1995-01-28
1995-02-04
1995-02-11
1995-02-18
1995-02-25
1995-03-04
1995-03-11
1995-03-18
1995-03-25
1995-04-01
1995-04-08
1995-04-15
1995-04-22
1995-04-29
1995-05-06
1995-05-13
1995-05-20
1995-05-27
1995-06-03
1995-06-10
1995-06-17
1995-06-24
1995-07-01
1995-07-08
1995-07-15
1995-07-22
1995-07-29
1995-08-05
1995-08-12
1995-08-19
1995-08-26
1995-09-02
1995-09-09
1995-09-16
1995-09-23
1995-09-30
1995-10-07
1995-10-14
1995-10-21
1995-10-28
1995-11-04
1995-11-11
1995-11-18
1995-11-25
1995-12-02
1995-12-09
1995-12-16
1995-12-23
1995-12-30
1996-01-06
1996-01-13
1996-01-20
1996-01-27
1996-02-03
1996-02-10
1996-02-17
1996-02-24
1996-03-02
1996-03-09
1996-03-16
1996-03-23
1996-03-30
1996-04-06
1996-04-13
1996-04-20
1996-04-27
1996-05-04
1996-05-11
1996-05-18
1996-05-25
1996-06-01
1996-06-08
1996-06-15
1996-06-22
1996-06-29
1996-07-06
1996-07-13
1996-07-20
1996-07-27
1996-08-03
1996-08-10
1996-08-17
1996-08-24
1996-08-31
1996-09-07
1996-09-14
1996-09-21
1996-09-28

2000-11-25
2000-12-02
2000-12-09
2000-12-16
2000-12-23
2000-12-30
2001-01-06
2001-01-13
2001-01-20
2001-01-27
2001-02-03
2001-02-10
2001-02-17
2001-02-24
2001-03-03
2001-03-10
2001-03-17
2001-03-24
2001-03-31
2001-04-07
2001-04-14
2001-04-21
2001-04-28
2001-05-05
2001-05-12
2001-05-19
2001-05-26
2001-06-02
2001-06-09
2001-06-16
2001-06-23
2001-06-30
2001-07-07
2001-07-14
2001-07-21
2001-07-28
2001-08-04
2001-08-11
2001-08-18
2001-08-25
2001-09-01
2001-09-08
2001-09-15
2001-09-22
2001-09-29
2001-10-06
2001-10-13
2001-10-20
2001-10-27
2001-11-03
2001-11-10
2001-11-17
2001-11-24
2001-12-01
2001-12-08
2001-12-15
2001-12-22
2001-12-29
2002-01-05
2002-01-12
2002-01-19
2002-01-26
2002-02-02
2002-02-09
2002-02-16
2002-02-23
2002-03-02
2002-03-09
2002-03-16
2002-03-23
2002-03-30
2002-04-06
2002-04-13
2002-04-20
2002-04-27
2002-05-04
2002-05-11
2002-05-18
2002-05-25
2002-06-01
2002-06-08
2002-06-15
2002-06-22
2002-06-29
2002-07-06
2002-07-13
2002-07-20
2002-07-27
2002-08-03
2002-08-10
2002-08-17

2004-04-03
2004-04-10
2004-04-17
2004-04-24
2004-05-01
2004-05-08
2004-05-15
2004-05-22
2004-05-29
2004-06-05
2004-06-12
2004-06-19
2004-06-26
2004-07-03
2004-07-10
2004-07-17
2004-07-24
2004-07-31
2004-08-07
2004-08-14
2004-08-21
2004-08-28
2004-09-04
2004-09-11
2004-09-18
2004-09-25
2004-10-02
2004-10-09
2004-10-16
2004-10-23
2004-10-30
2004-11-06
2004-11-13
2004-11-20
2004-11-27
2004-12-04
2004-12-11
2004-12-18
2004-12-25
2005-01-01
2005-01-08
2005-01-15
2005-01-22
2005-01-29
2005-02-05
2005-02-12
2005-02-19
2005-02-26
2005-03-05
2005-03-12
2005-03-19
2005-03-26
2005-04-02
2005-04-09
2005-04-16
2005-04-23
2005-04-30
2005-05-07
2005-05-14
2005-05-21
2005-05-28
2005-06-04
2005-06-11
2005-06-18
2005-06-25
2005-07-02
2005-07-09
2005-07-16
2005-07-23
2005-07-30
2005-08-06
2005-08-13
2005-08-20
2005-08-27
2005-09-03
2005-09-10
2005-09-17
2005-09-24
2005-10-01
2005-10-08
2005-10-15
2005-10-22
2005-10-29
2005-11-05
2005-11-12
2005-11-19
2005-11-26
2005-12-03
2005-12-10
2005-12-17
2005-12-24

2007-08-04
2007-08-11
2007-08-18
2007-08-25
2007-09-01
2007-09-08
2007-09-15
2007-09-22
2007-09-29
2007-10-06
2007-10-13
2007-10-20
2007-10-27
2007-11-03
2007-11-10
2007-11-17
2007-11-24
2007-12-01
2007-12-08
2007-12-15
2007-12-22
2007-12-29
2008-01-05
2008-01-12
2008-01-19
2008-01-26
2008-02-02
2008-02-09
2008-02-16
2008-02-23
2008-03-01
2008-03-08
2008-03-15
2008-03-22
2008-03-29
2008-04-05
2008-04-12
2008-04-19
2008-04-26
2008-05-03
2008-05-10
2008-05-17
2008-05-24
2008-05-31
2008-06-07
2008-06-14
2008-06-21
2008-06-28
2008-07-05
2008-07-12
2008-07-19
2008-07-26
2008-08-02
2008-08-09
2008-08-16
2008-08-23
2008-08-30
2008-09-06
2008-09-13
2008-09-20
2008-09-27
2008-10-04
2008-10-11
2008-10-18
2008-10-25
2008-11-01
2008-11-08
2008-11-15
2008-11-22
2008-11-29
2008-12-06
2008-12-13
2008-12-20
2008-12-27
2009-01-03
2009-01-10
2009-01-17
2009-01-24
2009-01-31
2009-02-07
2009-02-14
2009-02-21
2009-02-28
2009-03-07
2009-03-14
2009-03-21
2009-03-28
2009-04-04
2009-04-11
2009-04-18
2009-04-25

2010-12-11
2010-12-18
2010-12-25
2011-01-01
2011-01-08
2011-01-15
2011-01-22
2011-01-29
2011-02-05
2011-02-12
2011-02-19
2011-02-26
2011-03-05
2011-03-12
2011-03-19
2011-03-26
2011-04-02
2011-04-09
2011-04-16
2011-04-23
2011-04-30
2011-05-07
2011-05-14
2011-05-21
2011-05-28
2011-06-04
2011-06-11
2011-06-18
2011-06-25
2011-07-02
2011-07-09
2011-07-16
2011-07-23
2011-07-30
2011-08-06
2011-08-13
2011-08-20
2011-08-27
2011-09-03
2011-09-10
2011-09-17
2011-09-24
2011-10-01
2011-10-08
2011-10-15
2011-10-22
2011-10-29
2011-11-05
2011-11-12
2011-11-19
2011-11-26
2011-12-03
2011-12-10
2011-12-17
2011-12-24
2011-12-31
2012-01-07
2012-01-14
2012-01-21
2012-01-28
2012-02-04
2012-02-11
2012-02-18
2012-02-25
2012-03-03
2012-03-10
2012-03-17
2012-03-24
2012-03-31
2012-04-07
2012-04-14
2012-04-21
2012-04-28
2012-05-05
2012-05-12
2012-05-19
2012-05-26
2012-06-02
2012-06-09
2012-06-16
2012-06-23
2012-06-30
2012-07-07
2012-07-14
2012-07-21
2012-07-28
2012-08-04
2012-08-11
2012-08-18
2012-08-25
2012-09-01

...

2001-07-07
2001-07-14
2001-07-21
2001-07-28
2001-08-04
2001-08-11
2001-08-18
2001-08-25
2001-09-01
2001-09-08
2001-09-15
2001-09-22
2001-09-29
2001-10-06
2001-10-13
2001-10-20
2001-10-27
2001-11-03
2001-11-10
2001-11-17
2001-11-24
2001-12-01
2001-12-08
2001-12-15
2001-12-22
2001-12-29
2002-01-05
2002-01-12
2002-01-19
2002-01-26
2002-02-02
2002-02-09
2002-02-16
2002-02-23
2002-03-02
2002-03-09
2002-03-16
2002-03-23
2002-03-30
2002-04-06
2002-04-13
2002-04-20
2002-04-27
2002-05-04
2002-05-11
2002-05-18
2002-05-25
2002-06-01
2002-06-08
2002-06-15
2002-06-22
2002-06-29
2002-07-06
2002-07-13
2002-07-20
2002-07-27
2002-08-03
2002-08-10
2002-08-17
2002-08-24
2002-08-31
2002-09-07
2002-09-14
2002-09-21
2002-09-28
2002-10-05
2002-10-12
2002-10-19
2002-10-26
2002-11-02
2002-11-09
2002-11-16
2002-11-23
2002-11-30
2002-12-07
2002-12-14
2002-12-21
2002-12-28
2003-01-04
2003-01-11
2003-01-18
2003-01-25
2003-02-01
2003-02-08
2003-02-15
2003-02-22
2003-03-01
2003-03-08
2003-03-15
2003-03-22
2003-03-29

2008-04-26
2008-05-03
2008-05-10
2008-05-17
2008-05-24
2008-05-31
2008-06-07
2008-06-14
2008-06-21
2008-06-28
2008-07-05
2008-07-12
2008-07-19
2008-07-26
2008-08-02
2008-08-09
2008-08-16
2008-08-23
2008-08-30
2008-09-06
2008-09-13
2008-09-20
2008-09-27
2008-10-04
2008-10-11
2008-10-18
2008-10-25
2008-11-01
2008-11-08
2008-11-15
2008-11-22
2008-11-29
2008-12-06
2008-12-13
2008-12-20
2008-12-27
2009-01-03
2009-01-10
2009-01-17
2009-01-24
2009-01-31
2009-02-07
2009-02-14
2009-02-21
2009-02-28
2009-03-07
2009-03-14
2009-03-21
2009-03-28
2009-04-04
2009-04-11
2009-04-18
2009-04-25
2009-05-02
2009-05-09
2009-05-16
2009-05-23
2009-05-30
2009-06-06
2009-06-13
2009-06-20
2009-06-27
2009-07-04
2009-07-11
2009-07-18
2009-07-25
2009-08-01
2009-08-08
2009-08-15
2009-08-22
2009-08-29
2009-09-05
2009-09-12
2009-09-19
2009-09-26
2009-10-03
2009-10-10
2009-10-17
2009-10-24
2009-10-31
2009-11-07
2009-11-14
2009-11-21
2009-11-28
2009-12-05
2009-12-12
2009-12-19
2009-12-26
2010-01-02
2010-01-09
2010-01-16

2014-02-22
2014-03-01
2014-03-08
2014-03-15
2014-03-22
2014-03-29
2014-04-05
2014-04-12
2014-04-19
2014-04-26
2014-05-03
2014-05-10
2014-05-17
2014-05-24
2014-05-31
2014-06-07
2014-06-14
2014-06-21
2014-06-28
2014-07-05
2014-07-12
2014-07-19
2014-07-26
2014-08-02
2014-08-09
2014-08-16
2014-08-23
2014-08-30
2014-09-06
2014-09-13
2014-09-20
2014-09-27
2014-10-04
2014-10-11
2014-10-18
2014-10-25
2014-11-01
2014-11-08
2014-11-15
2014-11-22
2014-11-29
2014-12-06
2014-12-13
2014-12-20
2014-12-27
2015-01-03
2015-01-10
2015-01-17
2015-01-24
2015-01-31
2015-02-07
2015-02-14
2015-02-21
2015-02-28
2015-03-07
2015-03-14
2015-03-21
2015-03-28
2015-04-04
2015-04-11
2015-04-18
2015-04-25
2015-05-02
2015-05-09
2015-05-16
2015-05-23
2015-05-30
2015-06-06
2015-06-13
2015-06-20
2015-06-27
2015-07-04
2015-07-11
2015-07-18
2015-07-25
2015-08-01
2015-08-08
2015-08-15
2015-08-22
2015-08-29
2015-09-05
2015-09-12
2015-09-19
2015-09-26
2015-10-03
2015-10-10
2015-10-17
2015-10-24
2015-10-31
2015-11-07
2015-11-14

1995-09-30
1995-10-07
1995-10-14
1995-10-21
1995-10-28
1995-11-04
1995-11-11
1995-11-18
1995-11-25
1995-12-02
1995-12-09
1995-12-16
1995-12-23
1995-12-30
1996-01-06
1996-01-13
1996-01-20
1996-01-27
1996-02-03
1996-02-10
1996-02-17
1996-02-24
1996-03-02
1996-03-09
1996-03-16
1996-03-23
1996-03-30
1996-04-06
1996-04-13
1996-04-20
1996-04-27
1996-05-04
1996-05-11
1996-05-18
1996-05-25
1996-06-01
1996-06-08
1996-06-15
1996-06-22
1996-06-29
1996-07-06
1996-07-13
1996-07-20
1996-07-27
1996-08-03
1996-08-10
1996-08-17
1996-08-24
1996-08-31
1996-09-07
1996-09-14
1996-09-21
1996-09-28
1996-10-05
1996-10-12
1996-10-19
1996-10-26
1996-11-02
1996-11-09
1996-11-16
1996-11-23
1996-11-30
1996-12-07
1996-12-14
1996-12-21
1996-12-28
1997-01-04
1997-01-11
1997-01-18
1997-01-25
1997-02-01
1997-02-08
1997-02-15
1997-02-22
1997-03-01
1997-03-08
1997-03-15
1997-03-22
1997-03-29
1997-04-05
1997-04-12
1997-04-19
1997-04-26
1997-05-03
1997-05-10
1997-05-17
1997-05-24
1997-05-31
1997-06-07
1997-06-14
1997-06-21

1999-11-27
1999-12-04
1999-12-11
1999-12-18
1999-12-25
2000-01-01
2000-01-08
2000-01-15
2000-01-22
2000-01-29
2000-02-05
2000-02-12
2000-02-19
2000-02-26
2000-03-04
2000-03-11
2000-03-18
2000-03-25
2000-04-01
2000-04-08
2000-04-15
2000-04-22
2000-04-29
2000-05-06
2000-05-13
2000-05-20
2000-05-27
2000-06-03
2000-06-10
2000-06-17
2000-06-24
2000-07-01
2000-07-08
2000-07-15
2000-07-22
2000-07-29
2000-08-05
2000-08-12
2000-08-19
2000-08-26
2000-09-02
2000-09-09
2000-09-16
2000-09-23
2000-09-30
2000-10-07
2000-10-14
2000-10-21
2000-10-28
2000-11-04
2000-11-11
2000-11-18
2000-11-25
2000-12-02
2000-12-09
2000-12-16
2000-12-23
2000-12-30
2001-01-06
2001-01-13
2001-01-20
2001-01-27
2001-02-03
2001-02-10
2001-02-17
2001-02-24
2001-03-03
2001-03-10
2001-03-17
2001-03-24
2001-03-31
2001-04-07
2001-04-14
2001-04-21
2001-04-28
2001-05-05
2001-05-12
2001-05-19
2001-05-26
2001-06-02
2001-06-09
2001-06-16
2001-06-23
2001-06-30
2001-07-07
2001-07-14
2001-07-21
2001-07-28
2001-08-04
2001-08-11
2001-08-18